# Project

https://www.kaggle.com/c/kktv-data-game-1711

Original Training Data: (92951083, 12)


internet_connection_type (7, object): [cellular, cellular 2G, cellular 3G, cellular 4G, offline, online but unknown, wifi]
<br>
platform (3, object): [Android, Web, iOS]
<br>

action_trigger (14, object): [api error, cast, error, interrupt, ..., program stopped, program stopped or enlarged-reduced, seek, video ended]

<br>
最後一個training data的使用者user ID為57158  (data-045.csv)
最後一個label data的使用者user ID為57158  (label-045.csv)


/home/user/data/ML_SVN/DataScience/project

In [56]:
import sys  # handle command argument
import numpy as np
import matplotlib.pyplot as plt
from sklearn import preprocessing   #for normalization
from sklearn.model_selection import cross_val_score  # for cross validation
from sklearn import linear_model
from sklearn import  metrics # confusion matrix
from sklearn.model_selection import train_test_split
import itertools #  for  plot_confusion_matrix
import pandas as pd
import os, sys,glob
from pathlib import Path
from datetime import datetime,date
    

In [57]:
def process_time(stime):
    #'2017-11-24 7:59:25.334'
    time_slot=-1
    date1,time1= stime.split(' ')
    date1=[int(i) for i in date1.split('-')]   #[2017, 6, 8] Y/M/D
    time1=[float(i) for i in time1.split(':')]  #[15.0, 18.0, 25.334] H/M/S
    t=datetime(date1[0], date1[1],date1[2],int(time1[0]),int(time1[1])).time()

    t0=t.replace(hour=1,minute=0)
    t1=t.replace(hour=9,minute=0)
    t2=t.replace(hour=17,minute=0)
    t3=t.replace(hour=21,minute=0)
    #print(t)
    #print(t0)  #01:00:00

    if (t>=t0 and t<t1): #AM1:00~AM9:00
        time_slot=0
    elif (t>=t1 and t<t2):  #AM9:00~PM17:00
        time_slot=1
    elif (t>=t2 and t<t3): #PM17:00~PM9:00 
        time_slot=2
    else:  # >PM 9:00
        time_slot=3
    # weekday
    weekday=date(date1[0], date1[1],date1[2]).weekday()   #Modnday:0, Tuesday:1 ,...Sunday:6
    
    return weekday,time_slot




In [76]:
# load data

def read_csv(files):
    #column filter
    
    '''
    all column list:
    user_id,device_id,session_id,title_id,event_time,played_duration,
    action_trigger,platform,episode_number,series_total_episodes_count,internet_connection_type,is_trailer
    '''
    #olny use partial column
    cols=['user_id','event_time','played_duration']
    df=pd.read_csv(files,usecols=cols)
    return df



def preprocess_file(file,start_id):    
   
    df=read_csv(file)

    max_user_id=df.iloc[-1:, 0] # last row of column 0
    max_id=np.array(max_user_id, dtype=pd.Series)[0] # series to ndarray
    print(max_id)
    print(df.shape)
    
    

    user_timeslot_list=[]
    #output file 'data.csv'
    #should i should previous ...
    
    for i in range(start_id,max_id+1):
        user_df=df[df['user_id']==i]
        print(user_df.shape)
        n_events=user_df.shape[0] #number of row
        total_duration=0
        time_slot=[0]*28
        for row in user_df.itertuples(index=True):
            weekday,slot=process_time(getattr(row, "event_time"))
            #time_slot[weekday*4+slot]+=1 #event count in each timeslot
            t=getattr(row, "played_duration")
            time_slot[weekday*4+slot]+=t #event count in each timeslot
            total_duration+=t

        #print(i,n_events,total_duration,time_slot)
        #write file for each row
        if (i==0):
            #write header
            f.write('user_id,n_event,total_duratioin,')
            for index in range(len(time_slot)):
                f.write('slot_%d,' %index)
            f.write('\n')
                
        f.write('%d,%d,%d,' %(i,n_events,total_duration))
        for s in time_slot:
            f.write('%s,' %(str(s)))
        f.write('\n')
        
    return  max_id   #we know the last one

def preprocess_Xdata():
    start_id=-1
    print("concatenate all files")
    path = "public/" 
    allFiles=[]
    total_files=75
    global f
    f=open('data.csv', 'w')
    for i in range(total_files):
        buf = "data-%03d.csv"%(i+1)
        buf=os.path.join(path,buf)
        print(i,'------------------------')
        start_id=preprocess_file(buf,start_id+1)
        allFiles.append(buf)
    f.close()
   
    print(allFiles)

def preprocess_Ydata():
    print("concatenate all files")
    path = "public/" 
    allFiles=[]
    total_files=45
    #allFiles = glob.glob(os.path.join(path,"label-*.csv"))
    for i in range(total_files):
        buf = "label-%03d.csv"%(i+1)
        buf=os.path.join(path,buf)
        allFiles.append(buf)
        
    print(allFiles)
    df = pd.concat(map(pd.read_csv,allFiles))
    print(df.shape)
    print("save file")
    df.to_csv('all_label.csv', encoding='utf-8', index=False)
    print("save file all_label Successfully!")


def load_data(train_data_path,test_data_path):
    
    Train_Data = pd.read_csv(train_data_path, sep=',', header=None)
    Train_Data = np.array(Train_Data.values)
    
    X_train=Train_Data[:,:Train_Data.shape[1]-1]  # 0~(last column-1) are features
    Y_train=Train_Data[:,Train_Data.shape[1]-1]   # the last column is Y (target)

    #X_test = pd.read_csv(test_data_path, sep=',', header=None)
    #X_test = np.array(X_test.values)
    #print(X_test.shape)

    return (X_train, Y_train, X_test)

#write data
def save_data(data,output_file):
    print('write file....')
    path = Path(output_file)
    with open(output_file, 'w') as f:
        for i in data:
            #print(int(item[1]))  #[1] the probability of Spam. 
            f.write('%d\n' %i)
    return





In [ ]:
def main():

   
    preprocess_Xdata()
    preprocess_Ydata()
    ''' 
    20171126
    process data first
    
    '''
    return 

    
    # Load feature and label
    #X_all, Y_all, X_test=load_data('alldata.csv')


    print('X_all:',X_all.shape)
    print('X_test:',X_test.shape)
    #Normalization
    X_all =  preprocessing.scale(X_all)
    X_test = preprocessing.scale(X_test)
    #train & validation & test
    #Xtrain, Xvalid, ytrain, yvalid =train_test_split(X_all,Y_all, test_size = 0.1)


    #y=options[method](Xtrain,Xvalid,ytrain,yvalid,X_test)
    #save_data(y,'predict.csv')

    print('Finished !')


main()

concatenate all files
0 ------------------------
1250
(1188171, 3)
(91, 3)
0 91 16316 [0, 0, 0, 0, 0, 68, 0, 0, 0, 0, 0, 0, 0, 6873, 0, 0, 0, 0, 0, 0, 10, 2218, 0, 0, 7147, 0, 0, 0]
(1, 3)
1 1 9 [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 0, 0, 0, 0, 0, 0]
(29, 3)
2 29 6798 [0, 2687, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 417, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3663, 6, 25, 0]
(4021, 3)
3 4021 136712 [0, 15885, 710, 0, 2648, 12584, 0, 0, 82, 13391, 8344, 0, 5438, 7812, 9883, 0, 5366, 17414, 179, 0, 0, 2154, 0, 0, 6680, 15032, 13110, 0]
(3231, 3)
4 3231 590654 [23487, 53107, 0, 7964, 26083, 49045, 0, 8737, 25684, 39518, 0, 11009, 29808, 55151, 3309, 10276, 25760, 43092, 0, 8326, 41552, 53026, 3691, 5660, 31486, 34342, 0, 541]
(56, 3)
5 56 1684 [0, 79, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1605]
(3692, 3)
6 3692 666365 [5897, 65210, 1128, 3470, 25569, 91543, 111, 1121, 0, 114644, 18583, 0, 207, 66767, 3251, 0, 13679, 27686, 13273, 2738, 44

(32, 3)
77 32 6988 [0, 3378, 0, 0, 3531, 0, 0, 0, 79, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
(472, 3)
78 472 171109 [16875, 5498, 0, 1414, 3593, 4219, 0, 0, 19686, 6456, 0, 0, 19981, 7923, 0, 2081, 9498, 1149, 0, 0, 1807, 9109, 0, 0, 25754, 36066, 0, 0]
(7, 3)
79 7 13 [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 0, 0, 0, 0, 5, 0, 0, 0, 0, 0, 0]
(619, 3)
80 619 101839 [0, 0, 463, 0, 9006, 19246, 0, 0, 26074, 18383, 0, 182, 11946, 1348, 0, 2, 5844, 5875, 0, 0, 3328, 0, 0, 142, 0, 0, 0, 0]
(12, 3)
81 12 2557 [12, 0, 0, 0, 0, 2545, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
(15, 3)
82 15 15615 [0, 0, 0, 0, 0, 0, 0, 0, 3598, 910, 0, 0, 0, 0, 0, 0, 0, 8130, 2954, 0, 0, 0, 0, 0, 0, 23, 0, 0]
(6942, 3)
83 6942 218112 [12434, 34187, 1477, 0, 4, 17068, 0, 0, 2606, 25672, 0, 0, 0, 25032, 2367, 0, 0, 18651, 749, 0, 10029, 22381, 13865, 0, 8864, 22162, 564, 0]
(9565, 3)
84 9565 2427210 [49432, 148024, 40487, 12082, 64304, 198762, 47763, 9363, 86628, 2

(22755, 3)
148 22755 1358076 [58316, 59558, 14006, 3699, 146151, 133212, 20955, 5149, 67762, 71871, 28274, 17400, 147038, 124204, 4123, 6709, 82263, 52623, 17894, 4827, 71456, 46680, 19777, 10202, 57921, 48906, 30138, 6962]
(268, 3)
149 268 221225 [1278, 11621, 0, 3608, 8066, 21782, 0, 0, 1051, 16597, 0, 0, 5204, 16162, 0, 0, 5327, 21589, 33, 0, 4175, 28641, 3610, 0, 9594, 37536, 14467, 10884]
(140, 3)
150 140 131067 [0, 11343, 0, 0, 0, 14941, 0, 0, 0, 0, 0, 0, 0, 37108, 0, 0, 0, 21037, 9430, 0, 3335, 22132, 3552, 3071, 919, 0, 0, 4199]
(1078, 3)
151 1078 743947 [26091, 75542, 0, 0, 21451, 61359, 0, 0, 12223, 76722, 0, 0, 2325, 18642, 3256, 0, 11953, 80683, 11060, 0, 61276, 149928, 5340, 0, 8753, 112565, 4778, 0]
(35, 3)
152 35 22575 [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2054, 0, 8, 1882, 876, 0, 0, 0, 10040, 0, 0, 0, 5793, 0, 0, 1922, 0, 0]
(33, 3)
153 33 5724 [0, 455, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2869, 0, 0, 411, 1652, 0, 0, 0, 337, 0, 0]
(33, 3)
154 33 6455 [0, 138, 0, 0, 0

214 634 165676 [11940, 4104, 7926, 0, 401, 974, 13055, 0, 6163, 3838, 6942, 0, 561, 849, 1988, 0, 19149, 121, 13656, 2442, 12970, 8411, 12101, 937, 11020, 3727, 22401, 0]
(51, 3)
215 51 10968 [0, 23, 0, 0, 0, 0, 0, 0, 0, 3003, 0, 0, 942, 0, 0, 0, 3983, 0, 0, 0, 3017, 0, 0, 0, 0, 0, 0, 0]
(303, 3)
216 303 113711 [0, 6563, 0, 1277, 6046, 2254, 0, 100, 0, 8710, 0, 0, 324, 11299, 0, 2260, 10618, 9184, 0, 1118, 6066, 10066, 0, 0, 11525, 26301, 0, 0]
(48, 3)
217 48 1437 [424, 0, 0, 0, 0, 0, 0, 0, 0, 24, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 85, 904, 0]
(244, 3)
218 244 88968 [104, 0, 0, 0, 7751, 2701, 0, 1798, 16442, 5578, 9, 2, 7948, 16, 3174, 0, 7, 3040, 3426, 0, 6737, 11109, 7725, 0, 482, 10919, 0, 0]
(6593, 3)
219 6593 582744 [57435, 46633, 5321, 2523, 34215, 30436, 5900, 4728, 65940, 20843, 5437, 753, 42457, 14932, 9157, 2874, 43022, 31238, 8487, 0, 41362, 12580, 22707, 4334, 40958, 15817, 10121, 2534]
(381, 3)
220 381 121286 [0, 15119, 16216, 0, 0, 25013, 13844, 0, 169, 6839, 67

297 712 23594 [0, 2829, 0, 0, 0, 1257, 0, 0, 0, 279, 0, 0, 0, 89, 840, 0, 0, 119, 5211, 0, 0, 6828, 78, 0, 0, 2600, 3464, 0]
(12180, 3)
298 12180 2175224 [119059, 101282, 1168, 55204, 107321, 123108, 0, 54127, 145545, 110359, 221, 45641, 128197, 143937, 16548, 40989, 143511, 112469, 791, 64404, 155505, 130067, 13, 72036, 145134, 110012, 0, 48576]
(744, 3)
299 744 121100 [2412, 12993, 2002, 2046, 1963, 11319, 3753, 0, 0, 17661, 2749, 0, 2, 6898, 1134, 0, 0, 6431, 0, 1264, 4408, 10066, 0, 4866, 15577, 5825, 947, 6784]
(2140, 3)
300 2140 229222 [11842, 3046, 1993, 0, 0, 702, 18832, 0, 0, 15172, 10516, 0, 0, 23487, 22539, 4770, 628, 3810, 4473, 0, 0, 20060, 32537, 4111, 8582, 34738, 7384, 0]
(4, 3)
301 4 68 [0, 0, 0, 0, 68, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
(5017, 3)
302 5017 1282399 [19822, 126549, 100863, 43298, 0, 84808, 71254, 28251, 3926, 63418, 48377, 62532, 20859, 63749, 73439, 59232, 1519, 57064, 96168, 49402, 4500, 9331, 47374, 32428, 0, 11523, 7

...

40386 10415 1132362 [10690, 85784, 6107, 11625, 27301, 68547, 11211, 22756, 17468, 92053, 30374, 24096, 20300, 69948, 6293, 51607, 35682, 96531, 7405, 11005, 80066, 66020, 750, 57714, 79075, 91403, 20325, 30226]
(172, 3)
40387 172 77650 [18973, 0, 0, 0, 19038, 0, 0, 0, 13045, 0, 0, 0, 11154, 0, 0, 0, 11156, 1817, 0, 747, 0, 0, 0, 0, 0, 995, 725, 0]
(477, 3)
40388 477 133984 [10659, 7604, 0, 382, 934, 2938, 0, 53, 10814, 9186, 0, 0, 9945, 12136, 0, 1108, 3225, 7370, 2127, 0, 4534, 8918, 9310, 19, 20616, 9017, 0, 3089]
(1462, 3)
40389 1462 445789 [12188, 24249, 0, 0, 2258, 29165, 3937, 0, 23888, 46407, 1422, 0, 7315, 26845, 6079, 0, 32783, 41648, 16119, 8, 19009, 63958, 14129, 10768, 33808, 21400, 3588, 4818]
(9, 3)
40390 9 39 [35, 0, 0, 0, 0, 0, 0, 0, 0, 4, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
(1, 3)
40391 1 7 [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
(8895, 3)
40392 8895 610516 [53047, 81776, 13815, 0, 39584, 39936, 13589, 0, 

40461 8035 247782 [3600, 13116, 1890, 0, 0, 1579, 10378, 0, 11733, 22052, 12714, 3349, 9475, 25911, 7427, 0, 11458, 13902, 13817, 6607, 14736, 28035, 9638, 0, 2357, 13350, 10658, 0]
(32, 3)
40462 32 4637 [0, 26, 0, 0, 170, 0, 0, 0, 0, 0, 0, 0, 1792, 0, 0, 0, 2351, 0, 0, 0, 0, 0, 0, 0, 0, 298, 0, 0]
(99, 3)
40463 99 16092 [0, 5339, 0, 0, 3143, 0, 0, 0, 438, 2171, 0, 0, 4563, 0, 0, 0, 149, 0, 0, 0, 0, 289, 0, 0, 0, 0, 0, 0]
(242, 3)
40464 242 133615 [10856, 4529, 0, 3667, 5559, 9563, 0, 4949, 3617, 17270, 0, 0, 3926, 11639, 0, 1991, 6977, 1453, 0, 0, 9461, 15521, 0, 0, 14776, 7861, 0, 0]
(232, 3)
40465 232 136182 [7067, 1370, 0, 14512, 10995, 3764, 0, 28, 3980, 3592, 0, 6217, 5350, 0, 0, 5499, 13050, 48, 0, 13960, 12005, 2444, 0, 4094, 14551, 0, 0, 13656]
(68, 3)
40466 68 26034 [2913, 958, 0, 0, 852, 5716, 0, 0, 0, 0, 0, 0, 0, 1862, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5532, 5741, 2460, 0]
(279, 3)
40467 279 24219 [445, 0, 4321, 0, 2260, 1532, 1691, 0, 1745, 2041, 0, 0, 0, 0, 1851, 0, 0, 0, 0, 

40540 1628 360251 [19819, 16524, 2220, 0, 16939, 25782, 5281, 0, 10207, 24196, 1470, 0, 19096, 22524, 0, 0, 56659, 27304, 1432, 1806, 18515, 52549, 8666, 501, 15225, 10746, 2790, 0]
(811, 3)
40541 811 359072 [2339, 6306, 8333, 1178, 7511, 16946, 21409, 0, 13033, 21119, 28214, 0, 11251, 13480, 12762, 14121, 34134, 17613, 21690, 4343, 8363, 20363, 28119, 6447, 4516, 7017, 14775, 13690]
(18, 3)
40542 18 5278 [0, 0, 0, 0, 138, 0, 0, 0, 40, 0, 0, 0, 0, 1409, 0, 248, 0, 1912, 0, 0, 659, 27, 0, 0, 0, 0, 0, 845]
(12, 3)
40543 12 1028 [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 14, 0, 1009, 0, 0, 0, 0, 0, 5, 0, 0]
(2224, 3)
40544 2224 881223 [16687, 53093, 1093, 0, 45984, 59085, 7395, 1683, 58892, 61040, 4180, 2115, 71171, 72124, 3784, 0, 81160, 83757, 11484, 2127, 28152, 76912, 14840, 1260, 50797, 70310, 0, 2098]
(597, 3)
40545 597 93229 [4749, 4933, 2735, 0, 12420, 6094, 1, 0, 0, 1830, 0, 0, 3224, 7788, 4626, 0, 2033, 4550, 3262, 0, 4777, 5130, 3023, 4821, 8796, 2847, 2734, 2856]
(169

40606 15559 930189 [28383, 82127, 14890, 1569, 33074, 62992, 15716, 2285, 52262, 59644, 55653, 5071, 54615, 86798, 33185, 2996, 46375, 89429, 27512, 0, 20142, 41640, 4945, 0, 31039, 52121, 25726, 0]
(22, 3)
40607 22 6505 [0, 2981, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 18, 0, 0, 0, 0, 0, 0, 0, 517, 2989, 0, 0]
(398, 3)
40608 398 80038 [888, 4763, 177, 114, 4273, 9147, 0, 0, 3052, 10927, 4585, 1380, 1683, 6811, 12466, 1905, 2468, 4030, 0, 649, 1430, 7293, 878, 232, 709, 0, 0, 178]
(1, 3)
40609 1 1 [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0]
(72, 3)
40610 72 42585 [0, 0, 0, 0, 7263, 0, 0, 0, 0, 0, 0, 0, 11397, 0, 0, 0, 2698, 0, 0, 0, 7618, 1826, 0, 0, 466, 6878, 4439, 0]
(829, 3)
40611 829 314824 [14780, 26774, 9818, 0, 18653, 8720, 3168, 0, 41623, 9500, 0, 0, 27731, 9801, 13557, 0, 27443, 24150, 12388, 0, 17650, 19452, 0, 0, 12314, 15313, 1989, 0]
(19, 3)
40612 19 173 [0, 0, 0, 0, 0, 94, 0, 0, 0, 0, 0, 0, 3, 0, 0, 0, 0, 12, 0, 0, 0, 0, 64, 0, 

40695 12174 272670 [36750, 17035, 0, 1024, 20088, 5527, 3954, 780, 24574, 6859, 0, 743, 28300, 6268, 7661, 2717, 29103, 28670, 24390, 540, 8175, 4568, 2968, 0, 2540, 9428, 8, 0]
(59, 3)
40696 59 43473 [0, 0, 0, 0, 0, 0, 0, 0, 0, 4236, 3388, 0, 0, 12360, 8717, 0, 0, 7161, 7611, 0, 0, 0, 0, 0, 0, 0, 0, 0]
(3207, 3)
40697 3207 369282 [16585, 14904, 3808, 0, 20191, 11675, 2062, 0, 4355, 17810, 22370, 1451, 954, 20912, 9951, 0, 24361, 29164, 20110, 0, 3744, 27222, 32923, 0, 13192, 49261, 19746, 2531]
(551, 3)
40698 551 237649 [7699, 7019, 23982, 0, 2036, 39812, 6606, 0, 702, 11159, 20346, 0, 1391, 12452, 7927, 0, 6744, 24828, 15665, 0, 1796, 20960, 3620, 0, 1381, 11874, 9650, 0]
(1760, 3)
40699 1760 874698 [28074, 94044, 0, 0, 7236, 124061, 0, 0, 27933, 98391, 0, 0, 16555, 91899, 0, 0, 2919, 76398, 0, 0, 10245, 139353, 8348, 0, 31731, 117511, 0, 0]
(442, 3)
40700 442 337604 [13343, 23326, 13379, 348, 15826, 15370, 12918, 6926, 23846, 3202, 16261, 12238, 12891, 7736, 7701, 2741, 29669, 15322